In [1]:
%load_ext rpy2.ipython

In [2]:
%%R
set.seed(88888888) # maximum luck

library(DESeq2)
library(plotly)
library(ggplot2)
library(viridis)
library(magrittr)
library(pheatmap)
library(DescTools)
library(pdfCluster)
library(RColorBrewer)
library(SummarizedExperiment)
library(caret)
library(class)
library(htmlwidgets)

Loading required package: S4Vectors
Loading required package: stats4
Loading required package: BiocGenerics

Attaching package: ‘BiocGenerics’

The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs

The following objects are masked from ‘package:base’:

    anyDuplicated, aperm, append, as.data.frame, basename, cbind,
    colnames, dirname, do.call, duplicated, eval, evalq, Filter, Find,
    get, grep, grepl, intersect, is.unsorted, lapply, Map, mapply,
    match, mget, order, paste, pmax, pmax.int, pmin, pmin.int,
    Position, rank, rbind, Reduce, rownames, sapply, setdiff, sort,
    table, tapply, union, unique, unsplit, which.max, which.min


Attaching package: ‘S4Vectors’

The following object is masked from ‘package:utils’:

    findMatches

The following objects are masked from ‘package:base’:

    expand.grid, I, unname

Loading required package: IRanges
Loading required package: GenomicRanges
Loading required package: GenomeInfoDb
Loading require

In [3]:
%%R
OUT_DIR <- "/mnt/home/yuankeji/RanceLab/reticula_new/reticula/data/tcdd/output/"
N_FOLDS <- 10

In [4]:
%%R
vst.counts <- readRDS(paste(OUT_DIR, "vst_counts0.1vs0_time_course.Rds", sep = ""))
print(vst.counts)

class: DESeqTransform 
dim: 9297 90 
metadata(1): version
assays(1): ''
rownames(9297): ENSMUSG00000000001 ENSMUSG00000000028 ...
  ENSMUSG00000118462 ENSMUSG00000118541
rowData names(4): baseMean baseVar allZero dispFit
colnames(90): SRR7817611 SRR7817612 ... SRR4317629 SRR4317630
colData names(3): Sample Dose sizeFactor


In [5]:
%%R
sample <- colData(vst.counts)
# print(sample)

In [6]:
%%R
vst.count.mtx <-
   vst.counts %>% SummarizedExperiment::assay() %>% as.data.frame()
print(length(vst.count.mtx))
 head(vst.count.mtx)

[1] 90
                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000001  15.229012  15.249432  15.177854  15.273540  15.242004
ENSMUSG00000000028   8.223092   8.047147   8.350017   8.161974   8.247821
ENSMUSG00000000049  19.954035  19.933017  20.168155  20.139520  20.143586
ENSMUSG00000000058   8.947686   9.112121   9.153059   8.811928   9.445665
ENSMUSG00000000085  10.987383  10.701863  10.879763  10.879027  10.470498
ENSMUSG00000000088  16.479721  16.482798  16.447407  16.087556  16.032582
                   SRR7817623 SRR7817624 SRR7817625 SRR7817626 SRR7817627
ENSMUSG00000000001  15.151942  15.183428  15.362489  15.342864  15.118253
ENSMUSG00000000028   8.442488   8.212584   8.082460   8.286399   8.918388
ENSMUSG00000000049  20.158279  20.131709  20.071882  20.086730  20.097604
ENSMUSG00000000058   9.137306   9.565467   8.860541   9.066550   9.010738
ENSMUSG00000000085  10.661724  10.966817  11.075973  10.902767  10.534863
ENSMUSG00000000088  15.977229  

ENSMUSG00000000085  10.798010  10.807925  10.790537  10.929140  10.825994
ENSMUSG00000000088  15.476938  14.883475  14.747188  14.545462  14.825156
                   SRR4317626 SRR4317627 SRR4317607 SRR4317609 SRR4317610
ENSMUSG00000000001  14.787312  14.882170  14.454071  14.754122  14.893835
ENSMUSG00000000028   8.420865   8.477553   8.420726   8.751942   8.529019
ENSMUSG00000000049  20.332795  19.899198  20.284826  20.336640  20.348925
ENSMUSG00000000058   9.482830   9.298890   9.655910   9.817874  10.094255
ENSMUSG00000000085  10.643151  10.674890  11.065055  10.251842  10.679285
ENSMUSG00000000088  14.819435  14.219663  14.569121  14.188280  14.410528
                   SRR4317611 SRR4317612 SRR4317628 SRR4317629 SRR4317630
ENSMUSG00000000001  14.676405  14.531547  14.980280  15.024950  15.003661
ENSMUSG00000000028   8.856487   8.434915   8.535197   8.606901   8.843232
ENSMUSG00000000049  20.329689  20.330116  19.887789  20.286564  20.276110
ENSMUSG00000000058   9.582947   9.9400

In [7]:
%%R
tcdd_dose_detail.vec <-
   readRDS(paste(OUT_DIR, "tcdd_dose_detail_vec0.1vs0_time_course.Rds", sep = ""))
print(tcdd_dose_detail.vec)

 [1] 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
[20] 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
[39] 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
[58] 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.0 0.0 0.0 0.0 0.0 0.1 0.1 0.1
[77] 0.1 0.1 0.0 0.1 0.1 0.1 0.0 0.0 0.0 0.0 0.0 0.1 0.1 0.1


In [8]:
%%R
rxn2ensembls.nls <-
   readRDS(paste(OUT_DIR, "rxn2ensembls_nls0.1vs0_time_course.Rds", sep = ""))
print(length(rxn2ensembls.nls))
print(rxn2ensembls.nls)

[1] 9825
$`R-MMU-170666`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170671`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170674`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSM

 [46] "ENSMUSG00000028777" "ENSMUSG00000028950" "ENSMUSG00000028971"
 [49] "ENSMUSG00000029064" "ENSMUSG00000029072" "ENSMUSG00000029236"
 [52] "ENSMUSG00000029371" "ENSMUSG00000029372" "ENSMUSG00000029373"
 [55] "ENSMUSG00000029379" "ENSMUSG00000029380" "ENSMUSG00000029417"
 [58] "ENSMUSG00000029530" "ENSMUSG00000029663" "ENSMUSG00000029713"
 [61] "ENSMUSG00000029819" "ENSMUSG00000031778" "ENSMUSG00000031861"
 [64] "ENSMUSG00000031980" "ENSMUSG00000032192" "ENSMUSG00000032562"
 [67] "ENSMUSG00000032766" "ENSMUSG00000033717" "ENSMUSG00000034117"
 [70] "ENSMUSG00000034855" "ENSMUSG00000035042" "ENSMUSG00000035383"
 [73] "ENSMUSG00000035431" "ENSMUSG00000035448" "ENSMUSG00000036353"
 [76] "ENSMUSG00000036362" "ENSMUSG00000036381" "ENSMUSG00000036402"
 [79] "ENSMUSG00000036437" "ENSMUSG00000036832" "ENSMUSG00000037010"
 [82] "ENSMUSG00000037014" "ENSMUSG00000037140" "ENSMUSG00000037346"
 [85] "ENSMUSG00000037944" "ENSMUSG00000038607" "ENSMUSG00000038668"
 [88] "ENSMUSG00000038811" "ENSMUS

 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982019`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982020`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUS

 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000024325" "ENSMUSG00000025577" "ENSMUSG00000025578"
 [7] "ENSMUSG00000026021" "ENSMUSG00000026484" "ENSMUSG00000026739"
[10] "ENSMUSG00000028796" "ENSMUSG00000037652" "ENSMUSG00000039989"
[13] "ENSMUSG00000040669"

$`R-MMU-4570463`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020265" "ENSMUSG00000020738" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000031347"
[13] "ENSMUSG00000037652" "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MMU-4570499`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020738" "ENSMUSG00000021546" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000037652"
[13] "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MM

 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-3781943`
 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-205328`
[1] "ENSMUSG00000000127" "ENSMUSG00000005672" "ENSMUSG00000019966"
[4] "ENSMUSG00000032113" "ENSM

...

[1] "ENSMUSG00000032418"

$`R-MMU-109278`
[1] "ENSMUSG00000032420"

$`R-MMU-109291`
[1] "ENSMUSG00000032420"

$`R-MMU-8940070`
[1] "ENSMUSG00000032420"

$`R-MMU-8940074`
[1] "ENSMUSG00000032420"

$`R-MMU-4332235`
[1] "ENSMUSG00000032440" "ENSMUSG00000034342"

$`R-MMU-9756665`
[1] "ENSMUSG00000032446" "ENSMUSG00000062327" "ENSMUSG00000074637"

$`R-MMU-9756678`
[1] "ENSMUSG00000032446" "ENSMUSG00000042821" "ENSMUSG00000062327"

$`R-MMU-2399913`
[1] "ENSMUSG00000032454"

$`R-MMU-975629`
[1] "ENSMUSG00000032454" "ENSMUSG00000066441"

$`R-MMU-975633`
[1] "ENSMUSG00000032454"

$`R-MMU-200474`
[1] "ENSMUSG00000032456"

$`R-MMU-2161951`
[1] "ENSMUSG00000032487"

$`R-MMU-2309773`
[1] "ENSMUSG00000032487"

$`R-MMU-2309779`
[1] "ENSMUSG00000032487"

$`R-MMU-2309787`
[1] "ENSMUSG00000032487"

$`R-MMU-2314686`
[1] "ENSMUSG00000032487"

$`R-MMU-9018880`
[1] "ENSMUSG00000032487"

$`R-MMU-9020261`
[1] "ENSMUSG00000032487"

$`R-MMU-9026408`
[1] "ENSMUSG00000032487"

$`R-MMU-9027532`
[1] "ENSMUSG0000003

[1] "ENSMUSG00000033847"

$`R-MMU-1482696`
[1] "ENSMUSG00000033847"

$`R-MMU-1482816`
[1] "ENSMUSG00000033847" "ENSMUSG00000036257"

$`R-MMU-1482827`
[1] "ENSMUSG00000033847"

$`R-MMU-1482868`
[1] "ENSMUSG00000033847"

$`R-MMU-1482892`
[1] "ENSMUSG00000033847"

$`R-MMU-9603989`
[1] "ENSMUSG00000033849" "ENSMUSG00000034780" "ENSMUSG00000067370"
[4] "ENSMUSG00000074892"

$`R-MMU-1605530`
[1] "ENSMUSG00000033871" "ENSMUSG00000058440"

$`R-MMU-6813740`
[1] "ENSMUSG00000033917"

$`R-MMU-8953115`
[1] "ENSMUSG00000033943" "ENSMUSG00000038482" "ENSMUSG00000057469"
[4] "ENSMUSG00000059436"

$`R-MMU-444838`
[1] "ENSMUSG00000034009" "ENSMUSG00000039097" "ENSMUSG00000045232"

$`R-MMU-6785594`
[1] "ENSMUSG00000034023" "ENSMUSG00000039187"

$`R-MMU-199131`
[1] "ENSMUSG00000034028" "ENSMUSG00000040511"

$`R-MMU-199144`
[1] "ENSMUSG00000034028" "ENSMUSG00000062300"

$`R-MMU-434629`
[1] "ENSMUSG00000034116"

$`R-MMU-434634`
[1] "ENSMUSG00000034116"

$`R-MMU-879914`
[1] "ENSMUSG00000034116"

$`R-MMU-912

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 "ENSMUSG00000038224" "ENSMUSG00000059481"

$`R-MMU-202726`
[1] "ENSMUSG00000038235"

$`R-MMU-9717432`
[1] "ENSMUSG00000038260"

$`R-MMU-434989`
[1] "ENSMUSG00000038264" "ENSMUSG00000074785"

$`R-MMU-9649963`
[1] "ENSMUSG00000038276"

$`R-MMU-6784959`
[1] "ENSMUSG00000038286"

$`R-MMU-8985270`
[1] "ENSMUSG00000038331" "ENSMUSG00000039153"

$`R-MMU-1222685`
[1] "ENSMUSG00000038357"

$`R-MMU-6801687`
[1] "ENSMUSG00000038357" "ENSMUSG00000057729"

$`R-MMU-6787632`
[1] "ENSMUSG00000038372"

$`R-MMU-8953111`
[1] "ENSMUSG00000038482" "ENSMUSG00000057469"

$`R-MMU-199626`
[1] "ENSMUSG00000038496" "ENSMUSG00000040918"

$`R-MMU-9705794`
[1] "ENSMUSG00000038541"

$`R-MMU-374673`
[1] "ENSMUSG00000038546"

$`R-MMU-209765`
[1] "ENSMUSG00000038567"

$`R-MMU-211950`
[1] "ENSMUSG00000038567"

$`R-MMU-192033`
[1] "ENSMUSG00000038641"

$`R-MMU-192067`
[1] "ENSMUSG00000038641"

$`R-MMU-193746`
[1] "ENSMUSG00000038641"

$`R-MMU-193755`
[1] "ENSMUSG00000038641"

$`R-MMU-193821`
[1] "ENSMUSG00000038641"

$`

[1] "ENSMUSG00000040693"

$`R-MMU-211874`
[1] "ENSMUSG00000040703"

$`R-MMU-350604`
[1] "ENSMUSG00000040706"

$`R-MMU-373717`
[1] "ENSMUSG00000040760" "ENSMUSG00000060534"

$`R-MMU-1482961`
[1] "ENSMUSG00000040774"

$`R-MMU-1482962`
[1] "ENSMUSG00000040774" "ENSMUSG00000075703"

$`R-MMU-264418`
[1] "ENSMUSG00000040782"

$`R-MMU-264435`
[1] "ENSMUSG00000040782" "ENSMUSG00000059552"

$`R-MMU-4167511`
[1] "ENSMUSG00000040820" "ENSMUSG00000042010"

$`R-MMU-5635102`
[1] "ENSMUSG00000040836"

$`R-MMU-3209159`
[1] "ENSMUSG00000040857"

$`R-MMU-1471338`
[1] "ENSMUSG00000040899" "ENSMUSG00000044748" "ENSMUSG00000046354"
[4] "ENSMUSG00000059230"

$`R-MMU-1299338`
[1] "ENSMUSG00000040901"

$`R-MMU-5694583`
[1] "ENSMUSG00000040997"

$`R-NUL-9830947`
[1] "ENSMUSG00000040998"

$`R-MMU-5423117`
 [1] "ENSMUSG00000041229" "ENSMUSG00000060093" "ENSMUSG00000060639"
 [4] "ENSMUSG00000060678" "ENSMUSG00000060981" "ENSMUSG00000061482"
 [7] "ENSMUSG00000064288" "ENSMUSG00000067455" "ENSMUSG00000069266"
[10] 

In [9]:
%%R
rxns <- rxn2ensembls.nls %>% names()

In [10]:
%%R
rxn_knn_misclass_rate.nls <- list()
rxn_knn_ari.nls <- list()
rxn_knn_ecount.nls <- list()
rxn_pca.nls <- list()
count <- 0

In [11]:
%%R
toi_indices <- seq(1,length(tcdd_dose_detail.vec))
print(toi_indices)

In [12]:
%%R
tcdd_dose_detail_vec_tis_of_interest <-
   tcdd_dose_detail.vec[toi_indices]
print(tcdd_dose_detail_vec_tis_of_interest)

In [13]:
%%R
vst.count.mtx.tis_of_interest <- vst.count.mtx[, toi_indices]
print(vst.count.mtx.tis_of_interest)

  14.630860  14.804988
ENSMUSG00000005625  15.397314  15.508030  15.700442  15.777457  15.903217
ENSMUSG00000005628   7.238718   7.717136   7.267234   7.488207   8.148301
ENSMUSG00000005667   9.027143   9.262068   8.823307   9.034369   8.746961
ENSMUSG00000005672  10.243072   9.807203   9.549384  10.065168   9.871143
ENSMUSG00000005677  16.899820  16.933524  16.281004  16.370253  16.862124
ENSMUSG00000005681  21.335620  21.344756  21.662322  21.670340  21.585843
ENSMUSG00000005682  13.219167  13.430949  13.778215  13.807260  13.734572
ENSMUSG00000005683  16.391649  16.271598  15.896311  16.009460  16.103974
ENSMUSG00000005686   8.729344   8.109456   8.176107   8.354970   8.776818
ENSMUSG00000005687  12.663401  12.811704  13.047118  12.701378  12.891683
ENSMUSG00000005698  12.836972  12.828598  12.805114  12.953275  12.803030
ENSMUSG00000005699   9.307894   9.481740   9.302396   8.989014   9.454683
ENSMUSG00000005705   7.446709   7.717136   7.891572   7.488207   7.525209
ENSMUSG00000005

ENSMUSG00000006906  11.775200  11.880971  11.579677  11.390974  11.606167
ENSMUSG00000006932  16.921727  16.913354  16.989996  16.968038  16.986687
ENSMUSG00000006998  16.110425  16.199517  16.067592  16.189674  16.321221
ENSMUSG00000007033   8.569410   9.020943   9.095130   9.201675   9.468372
ENSMUSG00000007034   7.446709   7.236258   6.740089   6.897304   7.483646
ENSMUSG00000007038  13.976421  14.063702  13.685721  13.728217  13.637940
ENSMUSG00000007050  10.999163  11.324139  11.490536  11.613460  11.641109
ENSMUSG00000007080   9.026416   9.184276   8.720739   9.024586   8.689343
ENSMUSG00000007097   7.598140   7.236258   7.986992   7.773448   7.641383
ENSMUSG00000007107   7.177772   6.733329   7.272720   7.270278   7.266805
ENSMUSG00000007122   7.456944   7.717136   7.780039   7.886958   7.630059
ENSMUSG00000007207   7.446709   8.001522   7.874664   8.253440   7.635744
ENSMUSG00000007216   9.521960   9.433302   9.290519   9.579124   9.837872
ENSMUSG00000007279   6.733785   6.7333

ENSMUSG00000009900   6.733785   6.733329   6.740089   6.739636   6.738991
ENSMUSG00000009905  12.110667  11.921440  11.692161  11.987179  11.696538
ENSMUSG00000009907  14.165661  14.226434  13.831659  14.029997  13.644765
ENSMUSG00000009927  14.355596  14.606214  14.781851  14.753825  14.624113
ENSMUSG00000009941   6.733785   6.733329   6.740089   6.739636   7.266805
ENSMUSG00000009995  13.272191  13.175540  13.534045  13.453453  13.311012
ENSMUSG00000010021   7.698356   7.761048   7.491414   7.488207   7.769841
ENSMUSG00000010025  17.229317  17.286414  17.271598  17.330817  17.474746
ENSMUSG00000010045  11.665335  12.009292  12.037145  11.842967  11.933955
ENSMUSG00000010047  14.192546  14.208889  13.823885  13.825449  14.101640
ENSMUSG00000010051  14.763381  14.874169  14.856424  14.979888  14.707052
ENSMUSG00000010057  11.176912  11.561129  11.417093  11.888413  11.498849
ENSMUSG00000010064  20.171267  20.153978  19.786004  19.791818  19.725183
ENSMUSG00000010066   7.238718   7.2362

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



  10.866217
ENSMUSG00000016763   6.733785   6.733329   7.780039   7.775829   7.266805
ENSMUSG00000016833  11.720849  11.502616  11.635630  11.547167  11.220615
ENSMUSG00000016933  13.741567  13.951981  14.066816  14.043281  14.014929
ENSMUSG00000016942  18.496476  18.412076  18.327052  18.292305  18.483085
ENSMUSG00000016995   6.733785   6.733329   6.740089   6.739636   6.738991
ENSMUSG00000017002   8.827149   8.696308   7.868240   8.276468   8.599205
ENSMUSG00000017009  17.958993  17.902441  17.761629  17.785392  17.980429
ENSMUSG00000017057  14.568331  14.606214  13.789497  13.721146  13.143427
ENSMUSG00000017119  16.934480  16.891619  17.197043  17.164144  17.089187
ENSMUSG00000017132  13.746450  14.031325  12.999118  13.235229  13.264663
ENSMUSG00000017144  12.169263  12.084011  12.116761  12.144154  11.791511
ENSMUSG00000017146   8.502798   8.625120   8.794744   8.712185   8.411772
ENSMUSG00000017165   6.733785   6.733329   6.740089   6.739636   6.738991
ENSMUSG00000017167   9.128

...

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



  13.355783  13.406667
ENSMUSG00000005824   7.717232   8.001918   8.298901   7.597693   7.871233
ENSMUSG00000005836  10.366826  10.154660  10.570096   9.859215   9.783596
ENSMUSG00000005864   6.733340   6.733363   6.726850   6.724707   6.724574
ENSMUSG00000005871  12.976039  13.052687  13.469981  13.471835  13.528233
ENSMUSG00000005883   6.733340   7.231253   7.201278   6.724707   6.724574
ENSMUSG00000005886  13.735967  13.803147  13.668459  14.063184  14.147282
ENSMUSG00000005892   6.733340   6.733363   6.726850   6.724707   6.724574
ENSMUSG00000005893  13.877765  13.898626  13.641857  13.896136  14.003167
ENSMUSG00000005897  11.732631  11.730332  11.935671  11.579523  11.651694
ENSMUSG00000005899  11.988575  11.983986  11.723958  12.110044  11.940877
ENSMUSG00000005907  13.412840  13.576394  13.179730  13.577967  13.565631
ENSMUSG00000005947   8.330071   8.041817   7.390764   7.964387   7.629005
ENSMUSG00000005949  11.896767  11.692250  11.894026  11.935432  12.054301
ENSMUSG00000005

ENSMUSG00000014606  13.836713  13.819018  13.981463  13.966855  13.918275
ENSMUSG00000014609   7.236314   6.733363   7.201278   7.040322   7.635327
ENSMUSG00000014704   7.594433   7.823034   7.630478   7.381993   6.724574
ENSMUSG00000014763  12.391559  12.556543  12.524753  12.807502  12.716166
ENSMUSG00000014767  12.383379  12.402419  12.288644  12.383822  12.260763
ENSMUSG00000014769  15.419346  15.256184  14.999604  15.437853  15.522185
ENSMUSG00000014773   8.809832   8.943026   8.670660   9.673443   9.248654
ENSMUSG00000014786   7.876521   7.411956   8.480903   7.732768   8.217271
ENSMUSG00000014850  11.652847  11.503820  11.727856  11.771851  12.107954
ENSMUSG00000014852   9.614893   9.677275   9.888080  10.042681  10.111469
ENSMUSG00000014859  11.442462  11.440752  11.392245  10.984589  11.140108
ENSMUSG00000014867  16.929153  16.945729  17.376897  17.126711  17.079419
ENSMUSG00000014932  12.463329  12.347884  13.073430  12.850351  12.809634
ENSMUSG00000014956  15.978596  16.0014

ENSMUSG00000016283   7.236314   6.733363   7.196385   6.724707   6.724574
ENSMUSG00000016308  12.446783  12.780390  12.583542  12.492603  12.472490
ENSMUSG00000016319  17.426521  17.412233  16.875125  17.554493  17.601484
ENSMUSG00000016327   6.733340   6.733363   6.726850   6.724707   6.724574
ENSMUSG00000016356   8.405610   7.936210   9.184545   8.708644   8.552311
ENSMUSG00000016409  10.969257  11.064027  11.064301  10.849098  10.805116
ENSMUSG00000016427  13.598829  13.647187  14.408455  14.392360  14.276110
ENSMUSG00000016477  10.526118  10.847756  10.769146  10.655565  10.788143
ENSMUSG00000016487  13.378116  13.104177  13.280909  14.000541  14.103367
ENSMUSG00000016493  10.213460  10.388676  10.548761  10.001088  10.132006
ENSMUSG00000016494   8.597479   8.691479   8.699962   8.882573   8.364389
ENSMUSG00000016496   9.405665   9.091609   9.521729   8.465006   8.628269
ENSMUSG00000016498   6.733340   6.733363   6.726850   7.522375   6.724574
ENSMUSG00000016503  11.098145  11.3865

ENSMUSG00000018169   8.333665   8.452400   8.301048   8.184600   8.304923
ENSMUSG00000018189  11.736157  11.628144  11.973940  11.905317  11.878836
ENSMUSG00000018209  12.607224  12.625804  12.422879  12.347371  12.427429
ENSMUSG00000018263   6.733340   6.733363   6.726850   6.724707   6.724574
ENSMUSG00000018286  15.246062  15.114171  15.327975  15.488117  15.494821
ENSMUSG00000018293  14.670912  14.482452  15.305892  14.747544  14.652589
ENSMUSG00000018326  14.842016  14.887866  15.074379  14.965337  15.002165
ENSMUSG00000018334   8.771907   8.497168   8.684200   8.963323   8.912380
ENSMUSG00000018339   9.791256   9.972090   9.956678   9.560119   9.407720
ENSMUSG00000018340  15.443533  15.580945  15.286882  15.774529  15.819185
ENSMUSG00000018341   8.421281   8.273862   8.408596   8.631489   8.549813
ENSMUSG00000018347   9.903300   9.703291   9.699793   9.370619   9.487593
ENSMUSG00000018362  10.426262  10.239149  10.156323  10.505634  10.469588
ENSMUSG00000018363  14.070954  14.1864

In [14]:
%%R
training_indices <-
   caret::createDataPartition(
      tcdd_dose_detail_vec_tis_of_interest,
      times = 1,
      p = 1.0, # no data will be held out when set to "1.0"
      list = FALSE
   )
print(training_indices)

      Resample1
 [1,]         1
 [2,]         2
 [3,]         3
 [4,]         4
 [5,]         5
 [6,]         6
 [7,]         7
 [8,]         8
 [9,]         9
[10,]        10
[11,]        11
[12,]        12
[13,]        13
[14,]        14
[15,]        15
[16,]        16
[17,]        17
[18,]        18
[19,]        19
[20,]        20
[21,]        21
[22,]        22
[23,]        23
[24,]        24
[25,]        25
[26,]        26
[27,]        27
[28,]        28
[29,]        29
[30,]        30
[31,]        31
[32,]        32
[33,]        33
[34,]        34
[35,]        35
[36,]        36
[37,]        37
[38,]        38
[39,]        39
[40,]        40
[41,]        41
[42,]        42
[43,]        43
[44,]        44
[45,]        45
[46,]        46
[47,]        47
[48,]        48
[49,]        49
[50,]        50
[51,]        51
[52,]        52
[53,]        53
[54,]        54
[55,]        55
[56,]        56
[57,]        57
[58,]        58
[59,]        59
[60,]        60
[61,]        61
[62,]   

In [15]:
%%R
vst.count.mtx.train <-
   vst.count.mtx.tis_of_interest[, training_indices] #9/10ths of data
vst.count.mtx.test  <-
   vst.count.mtx.tis_of_interest[, -training_indices] #1/10th of data

print(vst.count.mtx.train)

                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000001  15.229012  15.249432  15.177854  15.273540  15.242004
ENSMUSG00000000028   8.223092   8.047147   8.350017   8.161974   8.247821
ENSMUSG00000000049  19.954035  19.933017  20.168155  20.139520  20.143586
ENSMUSG00000000058   8.947686   9.112121   9.153059   8.811928   9.445665
ENSMUSG00000000085  10.987383  10.701863  10.879763  10.879027  10.470498
ENSMUSG00000000088  16.479721  16.482798  16.447407  16.087556  16.032582
ENSMUSG00000000120  10.222778  10.291760  10.352682   9.899814   9.828669
ENSMUSG00000000126   7.935380   8.358822   7.783458   8.421341   8.237203
ENSMUSG00000000127  10.158849   9.929965  10.270600  10.153933  10.450689
ENSMUSG00000000142  10.367120  10.341324  10.321119  11.200972  10.916611
ENSMUSG00000000149  15.542206  15.623850  15.588207  15.725006  15.465996
ENSMUSG00000000154  14.918473  15.023581  15.119713  15.184469  15.201684
ENSMUSG00000000168  14.052225  14.0830

ENSMUSG00000001105  13.484356  13.487733  13.046051  13.100038  13.025747
ENSMUSG00000001119  10.250557   9.637547   9.917017  10.032418  10.582998
ENSMUSG00000001123  18.222463  18.199861  18.358494  18.402648  18.429766
ENSMUSG00000001127  14.567214  14.608134  14.825406  14.886743  15.010601
ENSMUSG00000001128  12.167261  12.310607  11.579834  11.866308  11.852563
ENSMUSG00000001131   7.246436   7.241655   6.721252   6.734609   7.821098
ENSMUSG00000001143  11.612742  11.409642  11.815187  11.797761  11.519642
ENSMUSG00000001155  18.686374  18.619990  18.758168  18.599354  18.562751
ENSMUSG00000001158  10.981698  10.761364  11.233230  10.763094  10.746331
ENSMUSG00000001173   9.992133  10.027791  10.547398  10.032418  10.477963
ENSMUSG00000001175  17.002562  17.025532  17.113560  17.214964  17.259766
ENSMUSG00000001211  16.658159  16.653746  16.660175  16.681082  16.633762
ENSMUSG00000001225   6.735215   7.236424   6.721252   6.734609   6.734558
ENSMUSG00000001228   8.023636   8.2341

ENSMUSG00000002249  11.116242  11.137398  11.280322  11.363629  11.065983
ENSMUSG00000002250  13.855186  14.004441  13.424426  14.225518  14.317129
ENSMUSG00000002257   7.734705   7.591750   7.662714   8.016525   7.929963
ENSMUSG00000002279  12.785868  13.225129  13.213019  13.433088  13.311388
ENSMUSG00000002289  12.304715  12.122700  13.529379  12.041177  12.300846
ENSMUSG00000002297   8.994226   9.162180   8.800939   8.721331   8.569930
ENSMUSG00000002307  11.314699  11.327507  11.379648  11.503976  11.503031
ENSMUSG00000002308   9.848386   9.809667   9.458914  10.094711   9.745510
ENSMUSG00000002324   8.847559   8.566214   9.314437   8.166254   8.419435
ENSMUSG00000002325  13.214160  13.309915  13.230058  13.599322  13.745538
ENSMUSG00000002326  11.593110  11.617405  11.348788  11.416976  11.539663
ENSMUSG00000002346  15.583354  15.619364  15.453105  15.517170  15.556875
ENSMUSG00000002365  13.263435  13.307773  13.639242  13.598177  13.668579
ENSMUSG00000002379  13.828834  13.5886

ENSMUSG00000003379   7.937192   8.156932   7.357270   7.930521   7.604568
ENSMUSG00000003402  15.626590  15.514599  15.638780  15.604100  15.472526
ENSMUSG00000003411   7.734705   8.081475   7.604175   8.016525   7.835218
ENSMUSG00000003418   6.735215   7.241655   7.357270   6.734609   7.242889
ENSMUSG00000003421  12.264448  12.488022  12.533015  12.423177  12.306454
ENSMUSG00000003429  14.190949  14.217523  13.875255  13.510033  13.616700
ENSMUSG00000003435  14.927759  14.890350  14.255523  14.690026  14.659095
ENSMUSG00000003436   6.735215   6.734329   6.721252   6.734609   6.734558
ENSMUSG00000003437  13.024397  12.835491  13.016603  12.767778  12.471195
ENSMUSG00000003444   9.638846   9.214028   9.753690   9.525017   9.888987
ENSMUSG00000003452   7.456867   7.447108   6.721252   6.734609   7.452200
ENSMUSG00000003458  13.528727  13.475355  13.315053  13.795281  13.733915
ENSMUSG00000003464  15.260448  15.415043  15.414772  15.481296  15.415829
ENSMUSG00000003476   7.610032   8.0132

ENSMUSG00000004654   6.735215   6.734329   6.721252   6.734609   6.734558
ENSMUSG00000004655  14.665994  14.654372  14.368766  14.632929  14.630037
ENSMUSG00000004665  10.200514   9.929523   9.859149  10.108971  10.472197
ENSMUSG00000004667  12.856527  13.043029  12.667325  12.513873  12.648399
ENSMUSG00000004668   6.735215   7.241655   6.721252   6.734609   6.734558
ENSMUSG00000004677  13.287706  13.287359  12.847647  13.014526  12.936539
ENSMUSG00000004709   7.246436   7.726454   7.357270   7.243163   7.814973
ENSMUSG00000004730  12.135249  12.179767  10.312877  11.577711  11.546089
ENSMUSG00000004768  10.839134  10.535732  10.854789  10.768126  10.802279
ENSMUSG00000004771  14.113119  14.242360  14.172262  14.113804  14.029268
ENSMUSG00000004788  12.119720  12.309874  11.949876  11.974090  12.008855
ENSMUSG00000004789  16.855382  16.870401  16.761383  16.808168  16.889622
ENSMUSG00000004791   7.246436   7.241655   6.721252   6.734609   6.734558
ENSMUSG00000004815  13.542039  13.4653

...

ENSMUSG00000006457   6.733340   6.733363   6.726850   8.025745   8.209557
ENSMUSG00000006464   9.171386   8.779998   9.141291   8.508028   8.461872
ENSMUSG00000006469   6.733340   6.733363   6.726850   6.724707   6.724574
ENSMUSG00000006494  14.762109  14.576793  13.481029  14.766055  14.772082
ENSMUSG00000006498  14.468352  14.470488  14.514400  14.628539  14.875427
ENSMUSG00000006517   9.765497  10.144576  10.382467  10.715094  10.849964
ENSMUSG00000006519  10.823263  10.564282  11.147248   9.615311   9.590879
ENSMUSG00000006522  19.913531  19.936539  20.837076  19.169502  19.199234
ENSMUSG00000006538   7.916563   7.443709   8.450968   8.036263   8.243321
ENSMUSG00000006542   8.091875   8.105482   7.773203   8.151186   7.793289
ENSMUSG00000006567  13.019642  13.087047  12.699505  13.464503  13.490168
ENSMUSG00000006574   8.079897   7.823034   7.397303   7.522375   7.733246
ENSMUSG00000006576   7.818825   8.001918   7.834992   7.149728   7.188996
ENSMUSG00000006585   9.240973   8.8601

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



  10.984589  11.140108
ENSMUSG00000014867  16.929153  16.945729  17.376897  17.126711  17.079419
ENSMUSG00000014932  12.463329  12.347884  13.073430  12.850351  12.809634
ENSMUSG00000014956  15.978596  16.001434  15.773287  16.032187  16.030159
ENSMUSG00000014959  15.026932  14.981731  15.049576  14.990273  15.065226
ENSMUSG00000015013  10.848106  11.105359  11.493666  11.278398  11.249618
ENSMUSG00000015016  12.647200  12.616559  12.222356  12.424684  12.426073
ENSMUSG00000015027  10.289769  10.629870  10.983311  10.395662  10.006179
ENSMUSG00000015053   7.822794   8.390088   7.923938   8.037570   8.158627
ENSMUSG00000015083  17.866564  17.813044  17.598959  17.813973  17.792356
ENSMUSG00000015085   9.431846   9.445899   9.509978   9.196645   9.373184
ENSMUSG00000015090   9.192960   9.810842  10.239808   9.649406   9.178431
ENSMUSG00000015094   9.517340   9.188907   9.883059   8.707901   9.086203
ENSMUSG00000015095  12.956486  12.682186  12.956362  12.914152  12.983638
ENSMUSG00000015

ENSMUSG00000016496   9.405665   9.091609   9.521729   8.465006   8.628269
ENSMUSG00000016498   6.733340   6.733363   6.726850   7.522375   6.724574
ENSMUSG00000016503  11.098145  11.386501  10.951020  11.180943  11.411794
ENSMUSG00000016524   6.733340   6.733363   6.726850   6.724707   6.724574
ENSMUSG00000016528  14.790845  14.531699  14.437531  14.407830  14.381579
ENSMUSG00000016529   6.733340   6.733363   7.540302   6.724707   6.724574
ENSMUSG00000016534  18.924423  18.923315  18.774217  18.965339  18.951003
ENSMUSG00000016554  14.584096  14.625852  14.037433  14.616013  14.513947
ENSMUSG00000016559  15.760851  15.704974  15.862242  15.355842  15.365056
ENSMUSG00000016619  13.314602  13.270766  13.222395  13.265507  13.269645
ENSMUSG00000016637  10.377949  10.635705  10.644582  10.505905  10.412980
ENSMUSG00000016664  13.364905  13.311376  13.336860  13.966855  14.163600
ENSMUSG00000016757  10.407209  10.294429  10.476803  10.661114  10.495833
ENSMUSG00000016763   7.236314   6.7333

ENSMUSG00000018347   9.903300   9.703291   9.699793   9.370619   9.487593
ENSMUSG00000018362  10.426262  10.239149  10.156323  10.505634  10.469588
ENSMUSG00000018363  14.070954  14.186411  13.998545  14.037783  14.277878
ENSMUSG00000018379  15.258029  15.221767  15.728599  15.416295  15.391900
ENSMUSG00000018395   8.931118   8.491921   9.342494   9.237642   9.284733
ENSMUSG00000018401  14.670533  14.792539  14.220270  14.483720  14.469503
ENSMUSG00000018411   9.463761   9.437467   9.143043   9.399094   9.647516
ENSMUSG00000018412  12.493811  12.661179  12.602177  12.974739  12.743975
ENSMUSG00000018428  15.980882  16.054371  15.567462  15.835601  15.789969
 [ reached 'max' / getOption("max.print") -- omitted 8186 rows ]


In [16]:
%%R
tcdd_dose_detail.vec.train <-
   tcdd_dose_detail_vec_tis_of_interest[training_indices]
tcdd_dose_detail.vec.test <-
   tcdd_dose_detail_vec_tis_of_interest[-training_indices]

# print(gtex_tissue_detail.vec.train)
print(length(unique(tcdd_dose_detail.vec.train)))

[1] 2


In [17]:
%%R
saveRDS(tcdd_dose_detail.vec.train,file=paste(OUT_DIR,"tcdd_dose_detail_vec_train0.1vs0_time_course.Rds",sep=""))

In [18]:
%%R
cv_fold_indices <- caret::createFolds(tcdd_dose_detail.vec.train,
                                      k = N_FOLDS)
print(cv_fold_indices)

$Fold01
[1] 15 23 27 34 44 49 63 65 86

$Fold02
[1]  1  2 12 31 46 57 58 69 85

$Fold03
[1]  8 10 11 16 22 29 30 43 74

$Fold04
[1]  3  6 32 35 41 48 55 60 84

$Fold05
[1]  4 18 36 51 53 61 64 89 90

$Fold06
[1]  9 13 19 25 37 56 71 77 88

$Fold07
[1]  7 14 17 40 52 59 79 82 87

$Fold08
[1] 24 26 38 39 66 68 72 73 80

$Fold09
[1]  5 21 42 47 50 62 70 75 83

$Fold10
[1] 20 28 33 45 54 67 76 78 81



In [19]:
%%R
binary_tcdd_dose_annotations <- unique(tcdd_dose_detail.vec)
print(binary_tcdd_dose_annotations)

[1] 0.0 0.1


In [20]:
%%R
full_rxn_pca_results.nls <- list()
rxn_id_2_result_file_idx.nls <- list()

In [21]:
%%R
n_rxns <- length(rxns)
print(n_rxns)
result_idx <- 1
for(rxn_id_idx in seq(1:n_rxns)){
   rxn_id <- rxns[rxn_id_idx]
   rxn_pca <-
      prcomp(t(vst.count.mtx.train[rxn2ensembls.nls[[rxn_id]], ]), scale. = T)
   full_rxn_pca_results.nls[[rxn_id]] <- rxn_pca
   rxn_id_2_result_file_idx.nls[[rxn_id]] <- result_idx
   rxn_pca.nls[[rxn_id]] <-
      rxn_pca$x[, 1] # 1st principal component coordinate within this reaction-space for each sample
   if(mod(rxn_id_idx,100) == 0){
      print(paste("Processed ",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      flush.console()
   }
   if(mod(rxn_id_idx,1000) == 0){
      print(paste("Storing PCA objects containing reactions ",rxn_id_idx-1000,
                  "-",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      saveRDS(full_rxn_pca_results.nls,
              paste(OUT_DIR, "full_rxn_pca_results_nls",rxn_id_idx-1000,
                    "-",rxn_id_idx,"0.1vs0_time_course.Rds", sep=""))
      full_rxn_pca_results.nls <- list()
      gc()
      result_idx <- result_idx + 1
   }
}

[1] 9825
[1] "Processed 100 of 9825 reactions (1%)..."
[1] "Processed 200 of 9825 reactions (2%)..."
[1] "Processed 300 of 9825 reactions (3.1%)..."
[1] "Processed 400 of 9825 reactions (4.1%)..."
[1] "Processed 500 of 9825 reactions (5.1%)..."
[1] "Processed 600 of 9825 reactions (6.1%)..."
[1] "Processed 700 of 9825 reactions (7.1%)..."
[1] "Processed 800 of 9825 reactions (8.2%)..."
[1] "Processed 900 of 9825 reactions (9.2%)..."
[1] "Processed 1000 of 9825 reactions (10.2%)..."
[1] "Storing PCA objects containing reactions 0-1000 of 9825 reactions (10.2%)..."
[1] "Processed 1100 of 9825 reactions (11.2%)..."
[1] "Processed 1200 of 9825 reactions (12.2%)..."
[1] "Processed 1300 of 9825 reactions (13.2%)..."
[1] "Processed 1400 of 9825 reactions (14.3%)..."
[1] "Processed 1500 of 9825 reactions (15.3%)..."
[1] "Processed 1600 of 9825 reactions (16.3%)..."
[1] "Processed 1700 of 9825 reactions (17.3%)..."
[1] "Processed 1800 of 9825 reactions (18.3%)..."
[1] "Processed 1900 of 9825 re

In [22]:
%%R
# store remaining PCA objects and removing from RAM
saveRDS(rxn_id_2_result_file_idx.nls,
        paste(OUT_DIR,"rxn_id_2_result_file_idx_nls0.1vs0_time_course.Rds",sep=""))
saveRDS(full_rxn_pca_results.nls,
        paste(OUT_DIR, "full_rxn_pca_results_nls0.1vs0_time_course.Rds", sep=""))
rm(full_rxn_pca_results.nls)
gc()

           used  (Mb) gc trigger  (Mb) max used  (Mb)
Ncells  6950693 371.3   13075688 698.4 11881756 634.6
Vcells 15907026 121.4   25842636 197.2 25842636 197.2


In [23]:
%%R
# compare informaction content of below files with pca plots or similar
saveRDS(rxn_pca.nls, paste(OUT_DIR, "rxn_pca_nls0.1vs0_time_course.Rds", sep = ""))
saveRDS(vst.count.mtx.train,
        paste(OUT_DIR, "vst_count_mtx_train0.1vs0_time_course.Rds", sep = ""))

In [24]:
%%R
for (cv_fold in names(cv_fold_indices)) {
  cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
}

In [25]:
%%R
# print(tissue_annotation)
# print(binary_tcdd_dose_annotations)
# print(paste("Processing tissue annotation:", tissue_annotation))
# print(length(binary_tcdd_dose_detail_vec.test.cv_test_list))
# print(sum(tcdd_dose_detail.vec.train.cv_test == tissue_annotation))
# print(length(rxns))

# binary_tcdd_dose_annotations <- c(0.00, 30.00, 0.01, 0.03, 0.10, 0.30, 1.00, 3.00, 10.00)

formatted_annotations <- format(binary_tcdd_dose_annotations, nsmall = 2)

formatted_annotations <- trimws(formatted_annotations)

binary_tcdd_dose_annotations <- formatted_annotations

print(binary_tcdd_dose_annotations)
for (annotation in binary_tcdd_dose_annotations) {
    print(annotation)
}

[1] "0.00" "0.10"
[1] "0.00"
[1] "0.10"


In [26]:
%%R
# main loop
for (rxn_id_idx in seq(1:length(rxns))) {
   rxn_id <- rxns[rxn_id_idx]
   ensembl_ids <- rxn2ensembls.nls[[rxn_id]]
   
   mean_misclass_rate <- list()
   sum_ari <- 0

   for (cv_fold in names(cv_fold_indices)) {
      cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
      
      vst.count.mtx.train.cv_train <-
         vst.count.mtx.train[, -cur_cv_fold_indices] # 4/5ths of training features
      vst.count.mtx.train.cv_test <-
         vst.count.mtx.train[, cur_cv_fold_indices] # 1/5th of training features
      
      tcdd_dose_detail.vec.train.cv_train <-
         tcdd_dose_detail.vec.train[-cur_cv_fold_indices] # 4/5ths of training labels
      tcdd_dose_detail.vec.train.cv_test <-
         tcdd_dose_detail.vec.train[cur_cv_fold_indices] # 1/5th of training labels
      
#        print(length(vst.count.mtx.train.cv_train))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
       
      binary_tcdd_dose_detail_vec.test.cv_test_list <- list()
      for (tissue_annotation in binary_tcdd_dose_annotations) {
#          print(tcdd_dose_detail.vec.train.cv_test)
#          print("-------------")
#          print(tissue_annotation)
#          print(binary_tcdd_dose_detail_vec.test.cv_test_list)
         binary_tcdd_dose_detail_vec.test.cv_test_list[[as.character(tissue_annotation)]] <-
            (as.character(tcdd_dose_detail.vec.train.cv_test) == as.character(tissue_annotation))
      }
      
      cv_train.expr_mat <-
         t(vst.count.mtx.train.cv_train[ensembl_ids, ])
      cv_test.expr_mat <-
         t(vst.count.mtx.train.cv_test[ensembl_ids, ])
#        print(dim(cv_train.expr_mat))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
      
      rxn_knn_calls <- class::knn(train = cv_train.expr_mat,
                                  test = cv_test.expr_mat,
                                  cl = tcdd_dose_detail.vec.train.cv_train)
      
      # calculate & store adjusted rand index
      cur_ari <- pdfCluster::adj.rand.index(rxn_knn_calls,
                                            tcdd_dose_detail.vec.train.cv_test)
      sum_ari <- cur_ari + sum_ari
      
      # for each tissue, calculate misclassification rate
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         cur_rxn_knn_calls <- (rxn_knn_calls == tissue_annotation)
            
         # calculate misclassification rate (https://stat.ethz.ch/pipermail/r-help/2011-September/288885.html)
         tab <- table(cur_rxn_knn_calls,
                      binary_tcdd_dose_detail_vec.test.cv_test_list[[tissue_annotation]])
        # print(tab)
         cur_misclass_rate <- 1 - sum(diag(tab)) / sum(tab)
        # print(paste("Misclass rate = 1 - ",sum(diag(tab))," / ",sum(tab)," = ", cur_misclass_rate,"...",sep=""))
         sum_misclass_rate <- cur_misclass_rate
         if (!is.null(mean_misclass_rate[[tissue_annotation]])) {
           sum_misclass_rate <- sum_misclass_rate + mean_misclass_rate[[tissue_annotation]]
         }
         mean_misclass_rate[[tissue_annotation]] <- sum_misclass_rate
      }
   }
   for(tissue_annotation in binary_tcdd_dose_annotations){
      mean_misclass_rate[[tissue_annotation]] <- (mean_misclass_rate[[tissue_annotation]] / N_FOLDS)
   }
   mean_ari <- sum_ari / N_FOLDS
   ecount <- length(ensembl_ids)
   
   rxn_knn_misclass_rate.nls[[rxn_id]] <- mean_misclass_rate
   assign("mean_misclass_rate",NULL,envir = .GlobalEnv)
   
   rxn_knn_ari.nls[[rxn_id]] <- mean_ari
   rxn_knn_ecount.nls[[rxn_id]] <- ecount
   
   count <- count + 1
   if (mod(count, 10) == 0) {
      print(
         paste(
            "Last RXN_ID = ",
            rxn_id,
            ": Last ARI = ",
            mean_ari,
            ": Last ECOUNT = ",
            ecount,
            ": Last Lung MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Lung"]],
            ": Last Uterus MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Uterus"]],
            ". Now ",
            round(1.0 - count / length(rxns),3) * 100,
            "% remaining..."
         )
      )
      flush.console()
   }
}

[1] "Last RXN_ID =  R-MMU-749456 : Last ARI =  0.699910157060166 : Last ECOUNT =  178 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9021601 : Last ARI =  0.524907311705207 : Last ECOUNT =  24 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3108203 : Last ARI =  0.662281049078945 : Last ECOUNT =  15 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9838627 : Last ARI =  0.285014406752062 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-193679 : Last ARI =  0.0722156464745721 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-194544 : Last ARI =  -0.0571985164878685 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.4 % remaining..."
[1] "L

[1] "Last RXN_ID =  R-MMU-8949580 : Last ARI =  0.751169937967834 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9692137 : Last ARI =  0.0531759997708956 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-450580 : Last ARI =  0.846318607764391 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-6791222 : Last ARI =  0.795614382412278 : Last ECOUNT =  61 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9696268 : Last ARI =  0.800901941097724 : Last ECOUNT =  41 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1912394 : Last ARI =  0.394867410315611 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.4 % remaining..."
[1] "L

[1] "Last RXN_ID =  R-MMU-3928599 : Last ARI =  -0.0915548083437953 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928625 : Last ARI =  0.216477347717802 : Last ECOUNT =  17 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928657 : Last ARI =  0.215083025079903 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9034539 : Last ARI =  0.0121738084928054 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-983156 : Last ARI =  0.846318607764391 : Last ECOUNT =  242 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-174119 : Last ARI =  0.606139817485906 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.4 % remaining..."
[1] 

[1] "Last RXN_ID =  R-MMU-3000411 : Last ARI =  0.783947715745612 : Last ECOUNT =  33 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-5228523 : Last ARI =  0.753591549295775 : Last ECOUNT =  33 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-2395328 : Last ARI =  0.0281603608820764 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-8852134 : Last ARI =  0.799444444444444 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-354124 : Last ARI =  0.733799045949054 : Last ECOUNT =  13 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-429415 : Last ARI =  0.733799045949054 : Last ECOUNT =  13 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.4 % remaining..."
[1] "La

[1] "Last RXN_ID =  R-MMU-5682377 : Last ARI =  0.557895431491223 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-2426496 : Last ARI =  0.465303638797615 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.8 % remaining..."
[1] "Last RXN_ID =  R-NUL-2467092 : Last ARI =  0.45414710485133 : Last ECOUNT =  7 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-168162 : Last ARI =  0.436429261498046 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-445079 : Last ARI =  0.422060926163039 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-8856808 : Last ARI =  0.701318607764391 : Last ECOUNT =  19 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.4 % remaining..."
[1] "Last R

...

[1] "Last RXN_ID =  R-NUL-1504194 : Last ARI =  0.128998794859833 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  20.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-437092 : Last ARI =  0.210426120064674 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  20 % remaining..."
[1] "Last RXN_ID =  R-MMU-173597 : Last ARI =  -0.0311787627337906 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-5663185 : Last ARI =  0.555465712615721 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-111285 : Last ARI =  0.0941649379053926 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9758661 : Last ARI =  0.860406885758998 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.6 % remaining..."
[1] "Last RX

[1] "Last RXN_ID =  R-MMU-5649725 : Last ARI =  -0.0560674594903222 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  15.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-9724745 : Last ARI =  0.0206800975353238 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  15 % remaining..."
[1] "Last RXN_ID =  R-MMU-9010872 : Last ARI =  0.0584641452189765 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-194641 : Last ARI =  -0.0483398312502808 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-202939 : Last ARI =  -0.0743916269949325 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9831009 : Last ARI =  0.150773304336065 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.6 % remaining..."
[1] "L

[1] "Last RXN_ID =  R-MMU-109759 : Last ARI =  0.0180760601089805 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  10.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-110352 : Last ARI =  0.0964803750431357 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  10 % remaining..."
[1] "Last RXN_ID =  R-MMU-975916 : Last ARI =  0.101578143560156 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-417858 : Last ARI =  0.182587447834139 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-446214 : Last ARI =  0.196932501666932 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-5578712 : Last ARI =  0.145421264963518 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.6 % remaining..."
[1] "Last RXN_ID = 

[1] "Last RXN_ID =  R-MMU-965067 : Last ARI =  0.293729345771599 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  5 % remaining..."
[1] "Last RXN_ID =  R-MMU-451056 : Last ARI =  -0.0106980479689626 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-1640164 : Last ARI =  0.285772196768294 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-1482897 : Last ARI =  -0.0662818856671733 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-5340195 : Last ARI =  0.159531633025609 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9708866 : Last ARI =  0.131487128625471 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.5 % remaining..."
[1] "Last RXN_ID

[1] "Last RXN_ID =  R-MMU-6786789 : Last ARI =  -0.0412192263281356 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  0.1 % remaining..."


In [27]:
%%R
saveRDS(
   rxn_knn_misclass_rate.nls,
   paste(OUT_DIR, "toi_rxn_knn_misclass_rate_nls0.1vs0_time_course.Rds", sep = "")
)
saveRDS(rxn_knn_ari.nls,
        paste(OUT_DIR, "toi_rxn_knn_ari_nls0.1vs0_time_course.Rds", sep = ""))
saveRDS(rxn_knn_ecount.nls,
        paste(OUT_DIR, "toi_rxn_knn_ecount_nls0.1vs0_time_course.Rds", sep = ""))

In [28]:
%%R
d <- data.frame(
   RXN_ID = names(rxn2ensembls.nls),
   MISCLASS = unlist(rxn_knn_misclass_rate.nls),
   ARI = unlist(rxn_knn_ari.nls),
   ECOUNT = unlist(rxn_knn_ecount.nls)
)
print(d)
saveRDS(d, paste(OUT_DIR, "toi_summary_df0.1vs0_time_course.Rds", sep = ""))

                          RXN_ID MISCLASS           ARI ECOUNT
R-MMU-170666.0.00   R-MMU-170666        0  5.106653e-01     14
R-MMU-170666.0.10   R-MMU-170671        0  5.106653e-01     14
R-MMU-170671.0.00   R-MMU-170674        0  5.106653e-01     14
R-MMU-170671.0.10   R-MMU-170686        0  5.106653e-01     14
R-MMU-170674.0.00   R-MMU-380073        0  6.999102e-01    182
R-MMU-170674.0.10   R-MMU-392187        0  4.398898e-01     22
R-MMU-170686.0.00   R-MMU-392195        0  4.398898e-01     22
R-MMU-170686.0.10   R-MMU-392202        0  4.398898e-01     22
R-MMU-380073.0.00   R-MMU-749454        0  6.999102e-01    178
R-MMU-380073.0.10   R-MMU-749456        0  6.999102e-01    178
R-MMU-392187.0.00   R-MMU-751001        0  4.416375e-01     21
R-MMU-392187.0.10  R-MMU-8964229        0  1.234025e-01      5
R-MMU-392195.0.00  R-MMU-8964242        0  1.234025e-01      5
R-MMU-392195.0.10  R-MMU-8964329        0  1.234025e-01      5
R-MMU-392202.0.00  R-MMU-8982012        0  5.990573e-01

R-MMU-205112.0.10  R-MMU-5654397        0  2.610506e-01     16
R-MMU-205117.0.00  R-MMU-5654399        0  2.610506e-01     16
R-MMU-205117.0.10  R-MMU-5654402        0  4.003240e-01     20
R-MMU-209532.0.00  R-MMU-5654404        0  1.482551e-01     16
R-MMU-209532.0.10  R-MMU-5654406        0  2.280479e-01     18
R-MMU-209566.0.00  R-MMU-5654407        0  1.482551e-01     16
R-MMU-209566.0.10  R-MMU-5654408        0  2.673559e-01     12
R-MMU-9012761.0.00 R-MMU-5654409        0  2.673559e-01     12
R-MMU-9012761.0.10 R-MMU-5654413        0  5.553943e-01     17
R-MMU-3247837.0.00 R-MMU-5654416        0  3.266958e-01     15
R-MMU-3247837.0.10 R-MMU-5654418        0  2.544986e-01     14
R-MMU-3247840.0.00 R-MMU-5654422        0  2.544986e-01     14
R-MMU-3247840.0.10 R-MMU-5654423        0  4.282007e-01     16
R-MMU-3247843.0.00 R-MMU-5654425        0  2.523246e-01     14
R-MMU-3247843.0.10 R-MMU-5654426        0  6.642860e-01     18
R-MMU-3247844.0.00 R-MMU-5654428        0  2.523246e-01

R-MMU-5654397.0.10 R-MMU-9753126        0  1.780212e-01      5
R-MMU-5654399.0.00  R-MMU-514604        0 -2.416542e-03      2
R-MMU-5654399.0.10  R-MMU-975389        0  3.502649e-01      4
R-MMU-5654402.0.00 R-MMU-1169394        0  4.931067e-01      5
R-MMU-5654402.0.10 R-MMU-1169398        0  5.126970e-01      5
R-MMU-5654404.0.00 R-MMU-1169402        0  5.995542e-01      6
R-MMU-5654404.0.10 R-MMU-1169403        0  3.596728e-01      4
R-MMU-5654406.0.00 R-MMU-1169405        0  6.457211e-01      5
R-MMU-5654406.0.10 R-MMU-1169406        0  5.180068e-01     12
R-MMU-5654407.0.00 R-MMU-1678842        0  7.168644e-01     13
R-MMU-5654407.0.10 R-MMU-1678843        0  4.444877e-01      5
R-MMU-5654408.0.00 R-MMU-5653754        0  7.168644e-01     21
R-MMU-5654408.0.10 R-MMU-5653756        0  7.506144e-01     19
R-MMU-5654409.0.00 R-MMU-9833973        0  3.991300e-01      5
R-MMU-5654409.0.10  R-MMU-426240        0  1.214881e-01     10
R-MMU-5654413.0.00  R-MMU-199050        0  2.428569e-01

R-MMU-5654664.0.10  R-MMU-389158        0  5.491345e-01      9
R-MMU-5654667.0.00  R-MMU-389348        0  7.282802e-03      8
R-MMU-5654667.0.10  R-MMU-389350        0  1.492265e-01      8
R-MMU-5654669.0.00  R-MMU-389352        0  1.315223e-01      7
R-MMU-5654669.0.10  R-MMU-389354        0  1.315223e-01      7
R-MMU-5654672.0.00  R-MMU-389381        0 -1.122439e-02      6
R-MMU-5654672.0.10  R-MMU-389758        0  5.728366e-01     22
R-MMU-5654673.0.00  R-MMU-389759        0  3.314973e-01      7
R-MMU-5654673.0.10  R-MMU-389762        0  1.265571e-01      5
R-MMU-5654677.0.00  R-MMU-434836        0  7.594972e-02      3
R-MMU-5654677.0.10  R-MMU-452100        0  2.777796e-02      6
R-MMU-5654679.0.00 R-MMU-8852200        0  3.457444e-01     17
R-MMU-5654679.0.10 R-MMU-8855381        0  4.823408e-01     18
R-MMU-5654684.0.00 R-MMU-8857925        0  7.845033e-01     15
R-MMU-5654684.0.10 R-MMU-9706312        0  2.481491e-01      2
R-MMU-5654690.0.00 R-MMU-8849348        0  3.236573e-01

R-MMU-9753126.0.10  R-MMU-450580        0  8.463186e-01     12
R-MMU-514604.0.00    R-MMU-72103        0  7.956144e-01     43
R-MMU-514604.0.10  R-MMU-9770119        0  7.506144e-01     69
R-MMU-975389.0.00  R-MMU-9770141        0  8.013186e-01    123
R-MMU-975389.0.10  R-MMU-9770142        0  7.506144e-01    132
R-MMU-1169394.0.00 R-MMU-9770145        0  7.506144e-01    145
R-MMU-1169394.0.10 R-MMU-9770236        0  8.013186e-01    119
R-MMU-1169398.0.00 R-MMU-6798748        0  8.733922e-01    106
R-MMU-1169398.0.10 R-MMU-6800434        0  8.733922e-01    134
R-MMU-1169402.0.00 R-MMU-6791218        0  8.333333e-01     68
R-MMU-1169402.0.10 R-MMU-6791222        0  7.956144e-01     61
R-MMU-1169403.0.00 R-MMU-1605595        0  5.759235e-01      3
R-MMU-1169403.0.10 R-MMU-1605624        0  2.301695e-01      6
R-MMU-1169405.0.00 R-MMU-1605717        0  1.213706e-01      1
R-MMU-1169405.0.10 R-MMU-6798751        0  7.168644e-01    105
R-MMU-1169406.0.00 R-MMU-9840795        0  7.403233e-02

...

R-NUL-9026445.0.00 R-MMU-8857692        0  1.234166e-01      2
R-NUL-9026445.0.10 R-MMU-4085217        0  1.651076e-01      1
R-NUL-9030427.0.00 R-MMU-5687090        0 -7.721762e-02      1
R-NUL-9030427.0.10 R-MMU-3134954        0  6.143503e-02      1
R-NUL-9033304.0.00  R-MMU-197235        0 -6.448005e-02      1
R-NUL-9033304.0.10 R-MMU-8939959        0 -6.448005e-02      1
R-NUL-9033333.0.00 R-MMU-2161791        0  1.925235e-01      3
R-NUL-9033333.0.10 R-MMU-2161959        0  1.925235e-01      3
R-MMU-443997.0.00  R-MMU-2161999        0  1.925235e-01      3
R-MMU-443997.0.10  R-MMU-3341277        0  2.347640e-01      1
R-MMU-391168.0.00  R-MMU-6805479        0  3.591518e-02      2
R-MMU-391168.0.10  R-MMU-9614414        0  7.593039e-01      3
R-MMU-8849638.0.00 R-MMU-9617657        0  2.185205e-01      1
R-MMU-8849638.0.10 R-MMU-9617711        0  2.185205e-01      1
R-MMU-8849646.0.00 R-MMU-9617755        0  2.185205e-01      1
R-MMU-8849646.0.10 R-NUL-9617710        0  2.185205e-01

R-MMU-2267372.0.00 R-MMU-1482897        0 -6.628189e-02      3
R-MMU-2267372.0.10 R-MMU-1482920        0  3.259123e-01      2
R-MMU-994137.0.00  R-MMU-9794031        0  3.661602e-01      1
R-MMU-994137.0.10   R-MMU-437240        0  6.879019e-02      1
R-MMU-994140.0.00   R-MMU-140355        0  2.654599e-01      1
R-MMU-994140.0.10   R-MMU-140359        0  2.654599e-01      1
R-MMU-2467775.0.00 R-MMU-2314678        0  2.654599e-01      1
R-MMU-2467775.0.10 R-MMU-9677320        0  2.654599e-01      1
R-MMU-5223305.0.00 R-MMU-6803890        0  1.354489e-01      1
R-MMU-5223305.0.10  R-MMU-947531        0 -4.073168e-03      1
R-MMU-8985201.0.00 R-MMU-5340195        0  1.595316e-01      1
R-MMU-8985201.0.10 R-MMU-6806674        0  2.400927e-02      1
R-MMU-196402.0.00   R-MMU-190681        0  4.046900e-01      1
R-MMU-196402.0.10  R-MMU-9846477        0  4.275765e-02      1
R-MMU-6807055.0.00 R-MMU-8850846        0  1.428309e-01      1
R-MMU-6807055.0.10 R-MMU-8850854        0  1.428309e-01

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 R-MMU-5649799        0  2.983957e-02     13
R-MMU-351210.0.00  R-MMU-5649801        0  2.983957e-02     13
R-MMU-351210.0.10  R-MMU-8847424        0  2.734971e-03      1
R-MMU-9012721.0.00  R-MMU-561253        0  1.950506e-01      1
R-MMU-9012721.0.10  R-MMU-428273        0  2.200502e-01      1
R-MMU-9013471.0.00 R-MMU-9836621        0  2.200502e-01      1
R-MMU-9013471.0.10  R-MMU-428779        0  2.990477e-01      1
R-MMU-9013533.0.00 R-MMU-8987120        0  4.689353e-02      1
R-MMU-9013533.0.10 R-MMU-8937442        0  7.839477e-01      2
R-MMU-9034756.0.00 R-MMU-1254376        0  1.853555e-02      1
R-MMU-9034756.0.10  R-MMU-211923        0  3.970059e-02      1
R-MMU-3299682.0.00  R-MMU-189423        0 -5.820915e-02      1
R-MMU-3299682.0.10 R-MMU-6786421        0  3.661602e-01      1
R-MMU-4837364.0.00  R-MMU-109341        0  7.073503e-02      1
R-MMU-4837364.0.10   R-MMU-77338        0  7.073503e-02      1
R-MMU-2161638.0.00   R-MMU-77345        0  7.073503e-02      1
R-MMU-2161

R-MMU-9756134.0.10 R-MMU-6788810        0 -5.645926e-02      1
R-MMU-9756156.0.00 R-MMU-8944246        0  2.147588e-01      1
R-MMU-9756156.0.10  R-MMU-420384        0 -6.902666e-02      1
R-MMU-9756183.0.00 R-MMU-6786239        0  1.724910e-01      1
R-MMU-9756183.0.10 R-MMU-9717434        0  2.323906e-01      1
R-MMU-9632038.0.00 R-MMU-5619427        0  3.004657e-01      1
R-MMU-9632038.0.10 R-MMU-1605723        0  9.027352e-02      1
R-MMU-9632039.0.00 R-MMU-4085029        0  9.027352e-02      1
R-MMU-9632039.0.10 R-MMU-8878787        0  4.275393e-01      1
R-MMU-5695989.0.00  R-MMU-162821        0  6.498947e-02      1
R-MMU-5695989.0.10 R-MMU-5619433        0  1.195509e-02      1
R-MMU-209821.0.00  R-MMU-6799977        0  5.547877e-02      1
R-MMU-209821.0.10  R-MMU-6799981        0  5.547877e-02      1
R-MMU-191323.0.00   R-MMU-174916        0  8.323611e-01      5
R-MMU-191323.0.10  R-MMU-8941701        0  8.323611e-01      3
R-MMU-159790.0.00   R-MMU-904864        0 -3.172019e-02

In [29]:
%%R
pid <- read.table(paste(OUT_DIR,"tcdd_project_id0.1vs0_time_course.txt",sep=""),header=FALSE)
sid <- read.table(paste(OUT_DIR,"tcdd_sample_id0.1vs0_time_course.txt",sep=""), header=FALSE)
sex <- read.table(paste(OUT_DIR, "tcdd_gender0.1vs0_time_course.txt", sep=""), header=FALSE)
print(sex)

       V1
1    male
2    male
3    male
4    male
5    male
6    male
7    male
8    male
9    male
10   male
11   male
12   male
13   male
14   male
15   male
16   male
17   male
18   male
19   male
20   male
21   male
22   male
23   male
24   male
25   male
26   male
27   male
28   male
29   male
30   male
31   male
32   male
33   male
34   male
35   male
36   male
37   male
38   male
39   male
40   male
41   male
42   male
43   male
44   male
45   male
46   male
47   male
48   male
49 female
50 female
51 female
52 female
53 female
54 female
55 female
56 female
57 female
58 female
59 female
60 female
61 female
62 female
63 female
64 female
65 female
66 female
67 female
68 female
69 female
70 female
71 female
72 female
73 female
74 female
75 female
76 female
77 female
78 female
79   male
80   male
81   male
82   male
83   male
84   male
85   male
86   male
87   male
88   male
89   male
90   male


In [30]:
%%R
library(htmlwidgets)
min_misclass_pca <-
   prcomp(t(vst.count.mtx.train), scale. = T)
pca.d <- data.frame(
   PC1 = min_misclass_pca$x[, 1],
   PC2 = min_misclass_pca$x[, 2],
   PC3 = min_misclass_pca$x[, 3],
   Section = tcdd_dose_detail.vec.train,
   Project_id = pid$V1,
   Sample_id = sid$V1
)

ggplot(pca.d, aes(x = PC1, y = PC2, colour = Section)) +
   geom_point(size = 3) +  # 绘制点，指定点的大小
   geom_text(aes(label = paste(Project_id, Sample_id)), vjust = -1, hjust = 1, size = 2) +  # 添加标签
   scale_colour_manual(values = c("0" = "red", "0.1" = "green")) +  # 手动指定颜色
   theme_bw()

p <- plot_ly(
   data = pca.d,
   x = ~PC1,
   y = ~PC2,
   z = ~PC3,
   type = "scatter3d",
   mode = "markers",
   marker = list(
     color = as.factor(pca.d$Section),  # 将 Section 转换为因子
     colors = c("red", "green"),  # 定义颜色
     size = 5
   ),
   text = ~paste("Project ID:", Project_id, "Sample ID:", Sample_id)  # 在悬停文本中显示 Project ID
)
saveWidget(p, "plotly_chart0.1vs0_time_course.html", selfcontained = TRUE)